In [ ]:
!pip install google-generativeai

In [1]:
import google.generativeai as genai
from google.colab import userdata
gemini_key = userdata.get('22_key')

genai.configure(api_key=gemini_key)


In [2]:
# configuration du modèle
generation_config = {
  "temperature": 0.9,
  "top_p": 1,
  "top_k": 5,
  "max_output_tokens": 2048,
}

In [3]:
# appel au modèle generative avec la configuration déjà fixée
model = genai.GenerativeModel(model_name= "gemini-1.0-pro",
                              generation_config = generation_config)

In [4]:
!pip install PyPDF2

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.6/232.6 kB 4.0 MB/s eta 0:00:00


In [5]:
#extractions de tout les fichiers

import PyPDF2
import os

def extraire_texte_pdf(chemin_fichier):
    """Extrait le texte d'un fichier PDF."""
    with open(chemin_fichier, 'rb') as fichier_pdf:
        lecteur = PyPDF2.PdfReader(fichier_pdf)
        texte = ""
        for page in lecteur.pages:
            texte += page.extract_text()
    return texte

# Liste des noms de fichiers PDF (à remplacer par vos noms de fichiers)
fichiers_pdf = ["/content/WEF_Global_Cybersecurity_Outlook_2024.pdf"]

# Chemin du fichier texte de sortie
chemin_fichier_sortie = "rcmdata.txt"

# Extraction et combinaison du texte
with open(chemin_fichier_sortie, 'w', encoding='utf-8') as fichier_sortie:
    for nom_fichier in fichiers_pdf:
        try:
            texte_extrait = extraire_texte_pdf(nom_fichier)
            fichier_sortie.write(texte_extrait)
            print(f"Texte extrait de '{nom_fichier}' et ajouté au fichier combiné.")
        except FileNotFoundError:
            print(f"Erreur : Fichier introuvable : '{nom_fichier}'")

print(f"Extraction terminée. Le texte combiné est enregistré dans '{chemin_fichier_sortie}'.")

Texte extrait de '/content/WEF_Global_Cybersecurity_Outlook_2024.pdf' et ajouté au fichier combiné.
Extraction terminée. Le texte combiné est enregistré dans 'rcmdata.txt'.


In [ ]:
 import time
import csv
import re
from google.api_core import exceptions

# ... (Code pour la définition du modèle 'model' avec "Gemini-1.0-pro")

def diviser_texte(texte, taille_chunk):
    """Divise un texte en chunks de taille spécifiée."""
    return [texte[i:i + taille_chunk] for i in range(0, len(texte), taille_chunk)]

def generer_questions_depuis_chunk(texte_chunk, nb_questions=2500):
    """Génère des questions à partir d'un chunk de texte."""

    prompt = f"""
    Génère {nb_questions} questions à partir de ce texte.
    Chaque question doit avoir 4 choix (A, B, C, D) et une seule réponse correcte.
    Les questions doivent être en français.
    Affiche la lettre correspondant à la réponse correcte après la question.

    Exemple :
    Question :  [Question]
    A. [Choix A]
    B. [Choix B]
    C. [Choix C]
    D. [Choix D]
    Réponse correcte : [Lettre de la bonne réponse]

    Texte:
    {texte_chunk}
    """

    questions = []
    while True:
        try:
            response = model.generate_content(prompt)
            # Supposons que chaque question est séparée par deux sauts de ligne
            questions_brutes = response.text.strip().split("\n\n")

            for question_brute in questions_brutes:
                # Extraction avec des expressions régulières (à adapter selon le format réel)
                match = re.match(r"Question :\s*(.*?)\nA.\s*(.*?)\nB.\s*(.*?)\nC.\s*(.*?)\nD.\s*(.*?)\nRéponse correcte :\s*(.*?)$", question_brute, re.DOTALL)
                if match:
                    question, a, b, c, d, reponse_correcte = match.groups()
                    questions.append([question.strip(), a.strip(), b.strip(), c.strip(), d.strip(), reponse_correcte.strip()])
                else:
                    print(f"Erreur de formatage de la question : {question_brute}")

            return questions

        except exceptions.TooManyRequests:
            print("Quota dépassé. Attente de 30 secondes...")
            time.sleep(30)
        except ValueError as e:
            print(f"Erreur de formatage de la réponse : {e}")
            return []  # Retourner une liste vide en cas d'erreur

# --- Code principal ---

nom_fichier_document = "rcmdata.txt"
nb_chunks = 1000

with open(nom_fichier_document, 'r', encoding='utf-8') as f:
    texte_complet = f.read()

taille_chunk = len(texte_complet) // nb_chunks
chunks = diviser_texte(texte_complet, taille_chunk)

with open('questions_reponses_generation.tsv', 'w', newline='', encoding='utf-8') as tsvfile:
    tsv_writer = csv.writer(tsvfile, delimiter='\t')
    tsv_writer.writerow(['Question', 'A', 'B', 'C', 'D', 'Réponse correcte'])

    for i, chunk in enumerate(chunks):
        questions = generer_questions_depuis_chunk(chunk, nb_questions=500)
        tsv_writer.writerows(questions)
        print(f"{len(questions)} questions générées à partir du chunk {i+1} et enregistrées.")

print("Génération des questions terminée.")

Le flux de sortie a été tronqué et ne contient que les 5000 dernières lignes.
**Réponse : B**
Erreur de formatage de la question : 3. Quelle est la tâche spécifique que l'IA est censée accomplir dans le texte ?
A. Générer du contenu original
B. Analyser de grandes quantités de données
C. Créer des simulations réalistes
D. Traduire les langues
**Réponse : B**
Erreur de formatage de la question : 4. Quelle est la nature des campagnes mentionnées dans le texte ?
A. Politiques
B. Militaires
C. Complexes
D. Simples
**Réponse : C**
Erreur de formatage de la question : 5. Quel est le but de commettre des campagnes convaincantes ?
A. Tromper les gens
B. Influencer l'opinion publique
C. Promouvoir des produits
D. Faire avancer une cause
**Réponse : B**
Erreur de formatage de la question : 6. Quelle est la principale contrainte dans l'utilisation de l'IA pour créer des deepfakes ?
A. La disponibilité des données d'entraînement
B. La puissance de calcul requise
C. Les implications éthiques
D. La 

In [ ]:
pip install selenium

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.7/9.7 MB 53.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 476.0/476.0 kB 27.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 4.0 MB/s eta 0:00:00


In [ ]:
options = webdriver.ChromeOptions()
options.add_argument("--remote-debugging-port=9222")  # Spécifiez un port de débogage
options.add_argument("--no-sandbox")  # Désactive le sandbox pour un débogage plus facile
options.add_argument("--disable-dev-shm-usage")  # Empêche les problèmes de mémoire partagée

In [ ]:
# Pseudo-code pour illustrer l'approche
import requests
from bs4 import BeautifulSoup

# Liste d'URLs de pages CVE et CWE
urls = ['https://nvd.nist.gov/cve/CVE-2023-1234',
        'https://nvd.nist.gov/cwe/CWE-79']

for url in urls:
    response = requests.get(url)
    soup = BeautifulSoup(response.content, 'html.parser')

    if "cve" in url:
        # Extraire les données de la vulnérabilité
        cve_id = soup.find('span', id='vulnId').text
        description = soup.find('p', attrs={'data-testid': 'vuln-description'}).text
        # ... extraire d'autres éléments pertinents

    elif "cwe" in url:
        # Extraire les données CWE
        cwe_id = soup.find('h2').text
        cwe_description = soup.find('p', class_='indent-0').text
        # ... extraire d'autres éléments pertinents

AttributeError: 'NoneType' object has no attribute 'text'

In [ ]:
from selenium import webdriver
from bs4 import BeautifulSoup

options = webdriver.ChromeOptions()
options.add_argument('--headless=new')  # Exécutez Chrome en mode headless

with webdriver.Chrome(options=options) as driver:
    driver.get(url)

    # Attendez que l'élément soit chargé (ajustez le sélecteur si nécessaire)
    driver.implicitly_wait(10)  # Attendez jusqu'à 10 secondes

    # Récupérez le code source HTML après le chargement dynamique
    soup = BeautifulSoup(driver.page_source, 'html.parser')

    # Extrayez l'élément
    cve_id = soup.find('span', id='vulnId').text  # Cela devrait maintenant fonctionner

SessionNotCreatedException: Message: session not created: Chrome failed to start: exited normally.
  (session not created: DevToolsActivePort file doesn't exist)
  (The process started from chrome location /root/.cache/selenium/chrome/linux64/129.0.6668.70/chrome is no longer running, so ChromeDriver is assuming that Chrome has crashed.)
Stacktrace:
#0 0x5a5c1c86510a <unknown>
#1 0x5a5c1c54b5e0 <unknown>
#2 0x5a5c1c583921 <unknown>
#3 0x5a5c1c57f2c5 <unknown>
#4 0x5a5c1c5cbdf6 <unknown>
#5 0x5a5c1c5cb446 <unknown>
#6 0x5a5c1c5bf8c3 <unknown>
#7 0x5a5c1c58d6b3 <unknown>
#8 0x5a5c1c58e68e <unknown>
#9 0x5a5c1c82fb0b <unknown>
#10 0x5a5c1c833a91 <unknown>
#11 0x5a5c1c81c305 <unknown>
#12 0x5a5c1c834612 <unknown>
#13 0x5a5c1c80146f <unknown>
#14 0x5a5c1c854008 <unknown>
#15 0x5a5c1c8541d3 <unknown>
#16 0x5a5c1c863f5c <unknown>
#17 0x7cca534d3ac3 <unknown>


In [ ]:
def diviser_fichier(nom_fichier, taille_chunk=100):
  """Divise un fichier texte en plusieurs fichiers de taille spécifiée.

  Args:
    nom_fichier: Le nom du fichier à diviser.
    taille_chunk: La taille maximale de chaque chunk en caractères.
  """

  with open(nom_fichier, 'r', encoding='utf-8') as fichier:
    contenu = fichier.read()

  num_chunk = 1
  for i in range(0, len(contenu), taille_chunk):
    chunk = contenu[i:i + taille_chunk]
    nom_chunk = f"chunk_{num_chunk}.txt"
    with open(nom_chunk, 'w', encoding='utf-8') as f:
      f.write(chunk)
    num_chunk += 1

# Exemple d'utilisation :
diviser_fichier("texte_combine.txt", 100)

In [ ]:
# Ouvrir le fichier en mode lecture ('r')
fichier = open("texte_combine.txt", "r")

# Lire le contenu du fichier
contenu = fichier.read()
print(contenu)

# Fermer le fichier (toujours important !)
fichier.close()

MITRE ATT&CKÒ: Design and Philosophy          Authors:  Blake E. Strom Andy Applebaum  Doug P. Miller Kathryn C. Nickels  Adam G. Pennington  Cody B. Thomas  Originally Published July 2018  Revised March 2020 MP180360R1 MITRE PRODUCT       
Project No.: 10AOH08A-JC  The views, opinions and/or findings contained in this report are those of The MITRE Corporation and should not be construed as an official government position, policy, or decision, unless designated by other documentation. Approved for Public Release. Distribution unlimited 19-01075-28.  ©2020 The MITRE Corporation.  All rights reserved. MITRE ATT&CK and ATT&CK are registered trademarks of the MITRE Corporation.  McLean, VA    iii ©2020 The MITRE Corporation. All Rights Reserved Approved for Public Release. Distribution unlimited 19-01075-28. Abstract MITRE ATT&CK is a globally-accessible knowledge base of adversary tactics and techniques based on real-world observations. The ATT&CK knowledge base is used as a foundation fo

In [ ]:
import time
import csv
from google.api_core import exceptions

# ... (Code pour la définition du modèle 'model' avec "Gemini-1.0-pro")

def generer_question_depuis_chunk(nom_fichier_chunk):
    """Génère une question à partir d'un fichier chunk."""

    with open(nom_fichier_chunk, 'r', encoding='utf-8') as f:
        texte_extrait = f.read()

    prompt = f"""
    Génère une seule question à partir de ce texte.
    La question doit avoir 4 choix (A, B, C, D) et une seule réponse correcte.
    La question doit être en français.
    Affiche la lettre correspondant à la réponse correcte après la question.

    Exemple :
    Question :  [Question]
    A. [Choix A]
    B. [Choix B]
    C. [Choix C]
    D. [Choix D]
    Réponse correcte : [Lettre de la bonne réponse]

    Texte:
    {texte_extrait}
    """

    while True:
        try:
            response = model.generate_content(prompt)
            question, reponse_correcte = response.text.strip().split("Réponse correcte :")
            return question.strip(), reponse_correcte.strip()
        except exceptions.TooManyRequests:
            print("Quota dépassé. Attente de 30 secondes...")
            time.sleep(30)
        except ValueError as e:
            print(f"Erreur de formatage de la réponse : {e}")
            return None, None

# --- Code principal ---

# Chemin vers les fichiers chunk (à adapter si nécessaire)
chemin_chunks = "./"
# Ouverture du fichier TSV en mode ajout ('a')
with open('questions_reponses_generation.tsv', 'a', newline='', encoding='utf-8') as tsvfile:
    tsv_writer = csv.writer(tsvfile, delimiter='\t')

    # Écrire l'en-tête uniquement si le fichier est vide
    if tsvfile.tell() == 0:
        tsv_writer.writerow(['Question', 'A','B','C','D','Réponse correcte'])

# Liste pour stocker les questions et réponses
#toutes_questions = []

# Boucle sur les 950 chunks
    for i in range(1,950):
        nom_fichier_chunk = f"{chemin_chunks}chunk_{i}.txt"

        question, reponse = generer_question_depuis_chunk(nom_fichier_chunk)
        if question and reponse:
          tsv_writer.writerow([question, reponse])  # Écrire la question et la réponse immédiatement
          print(f"Question {i} générée et enregistrée.")

#         toutes_questions.append([question, reponse])
#         print(f"Question {i} générée avec succès.")

# # Enregistrement dans un fichier TSV
# with open('questions_reponses_generation.tsv', 'w', newline='', encoding='utf-8') as tsvfile:
#     tsv_writer = csv.writer(tsvfile, delimiter='\t')  # Délimiteur '\t' pour TSV
#     tsv_writer.writerow(['Question', 'Réponse correcte'])  # En-tête
#     tsv_writer.writerows(toutes_questions)

print("Les questions et réponses ont été enregistrées dans 'questions_reponses_generation.tsv'")

Question 1 générée et enregistrée.
Question 2 générée et enregistrée.
Question 3 générée et enregistrée.
Question 4 générée et enregistrée.
Question 5 générée et enregistrée.
Question 6 générée et enregistrée.
Question 7 générée et enregistrée.
Question 8 générée et enregistrée.
Question 9 générée et enregistrée.
Question 10 générée et enregistrée.
Question 11 générée et enregistrée.
Question 12 générée et enregistrée.
Question 13 générée et enregistrée.
Question 14 générée et enregistrée.
Erreur de formatage de la réponse : not enough values to unpack (expected 2, got 1)
Question 16 générée et enregistrée.
Question 17 générée et enregistrée.
Question 18 générée et enregistrée.
Question 19 générée et enregistrée.
Question 20 générée et enregistrée.
Question 21 générée et enregistrée.


Quota dépassé. Attente de 30 secondes...
Question 22 générée et enregistrée.
Question 23 générée et enregistrée.
Question 24 générée et enregistrée.
Question 25 générée et enregistrée.
Question 26 générée et enregistrée.
Question 27 générée et enregistrée.
Question 28 générée et enregistrée.
Question 29 générée et enregistrée.
Question 30 générée et enregistrée.
Question 31 générée et enregistrée.
Question 32 générée et enregistrée.
Question 33 générée et enregistrée.
Question 34 générée et enregistrée.
Question 35 générée et enregistrée.
Question 36 générée et enregistrée.
Question 37 générée et enregistrée.


Quota dépassé. Attente de 30 secondes...
Question 38 générée et enregistrée.
Question 39 générée et enregistrée.
Question 40 générée et enregistrée.
Question 41 générée et enregistrée.
Question 42 générée et enregistrée.
Question 43 générée et enregistrée.
Question 44 générée et enregistrée.
Question 45 générée et enregistrée.
Question 46 générée et enregistrée.
Question 47 générée et enregistrée.
Question 48 générée et enregistrée.
Question 49 générée et enregistrée.
Question 50 générée et enregistrée.
Question 51 générée et enregistrée.
Question 52 générée et enregistrée.
Question 53 générée et enregistrée.


Quota dépassé. Attente de 30 secondes...
Question 54 générée et enregistrée.
Question 55 générée et enregistrée.
Question 56 générée et enregistrée.
Question 57 générée et enregistrée.
Question 58 générée et enregistrée.
Question 59 générée et enregistrée.
Question 60 générée et enregistrée.
Question 61 générée et enregistrée.
Question 62 générée et enregistrée.
Question 63 générée et enregistrée.
Question 64 générée et enregistrée.
Question 65 générée et enregistrée.
Question 66 générée et enregistrée.
Question 67 générée et enregistrée.
Question 68 générée et enregistrée.
Question 69 générée et enregistrée.


Quota dépassé. Attente de 30 secondes...
Question 70 générée et enregistrée.
Question 71 générée et enregistrée.
Question 72 générée et enregistrée.
Question 73 générée et enregistrée.
Question 74 générée et enregistrée.
Question 75 générée et enregistrée.
Question 76 générée et enregistrée.
Question 77 générée et enregistrée.
Question 78 générée et enregistrée.
Question 79 générée et enregistrée.
Question 80 générée et enregistrée.
Question 81 générée et enregistrée.
Question 82 générée et enregistrée.
Question 83 générée et enregistrée.
Question 84 générée et enregistrée.
Question 85 générée et enregistrée.
Question 86 générée et enregistrée.


...

Quota dépassé. Attente de 30 secondes...
Question 150 générée et enregistrée.
Question 151 générée et enregistrée.
Question 152 générée et enregistrée.
Question 153 générée et enregistrée.
Question 154 générée et enregistrée.
Question 155 générée et enregistrée.
Question 156 générée et enregistrée.
Question 157 générée et enregistrée.
Question 158 générée et enregistrée.
Question 159 générée et enregistrée.
Erreur de formatage de la réponse : not enough values to unpack (expected 2, got 1)
Question 161 générée et enregistrée.
Question 162 générée et enregistrée.
Erreur de formatage de la réponse : not enough values to unpack (expected 2, got 1)
Question 164 générée et enregistrée.
Question 165 générée et enregistrée.


Quota dépassé. Attente de 30 secondes...
Question 166 générée et enregistrée.
Question 167 générée et enregistrée.
Question 168 générée et enregistrée.
Question 169 générée et enregistrée.
Question 170 générée et enregistrée.
Question 171 générée et enregistrée.
Question 172 générée et enregistrée.
Question 173 générée et enregistrée.
Question 174 générée et enregistrée.
Question 175 générée et enregistrée.
Question 176 générée et enregistrée.
Question 177 générée et enregistrée.
Question 178 générée et enregistrée.
Question 179 générée et enregistrée.
Question 180 générée et enregistrée.
Question 181 générée et enregistrée.


Quota dépassé. Attente de 30 secondes...
Question 182 générée et enregistrée.
Question 183 générée et enregistrée.
Question 184 générée et enregistrée.
Question 185 générée et enregistrée.
Question 186 générée et enregistrée.
Question 187 générée et enregistrée.
Question 188 générée et enregistrée.
Question 189 générée et enregistrée.
Question 190 générée et enregistrée.
Question 191 générée et enregistrée.
Question 192 générée et enregistrée.
Question 193 générée et enregistrée.
Question 194 générée et enregistrée.
Question 195 générée et enregistrée.
Question 196 générée et enregistrée.


Quota dépassé. Attente de 30 secondes...
Erreur de formatage de la réponse : not enough values to unpack (expected 2, got 1)
Question 198 générée et enregistrée.
Question 199 générée et enregistrée.
Question 200 générée et enregistrée.
Question 201 générée et enregistrée.
Question 202 générée et enregistrée.
Question 203 générée et enregistrée.
Question 204 générée et enregistrée.
Question 205 générée et enregistrée.
Question 206 générée et enregistrée.
Question 207 générée et enregistrée.
Question 208 générée et enregistrée.
Question 209 générée et enregistrée.
Question 210 générée et enregistrée.
Question 211 générée et enregistrée.
Question 212 générée et enregistrée.
Question 213 générée et enregistrée.
Question 214 générée et enregistrée.
Question 215 générée et enregistrée.
Question 216 générée et enregistrée.
Question 217 générée et enregistrée.
Question 218 générée et enregistrée.
Erreur de formatage de la réponse : not enough values to unpack (expected 2, got 1)
Question 220 g

ReadTimeout: HTTPConnectionPool(host='localhost', port=36715): Read timed out. (read timeout=600.0)

In [ ]:
import os
print(os.listdir())  # Affiche les fichiers dans le répertoire de travail actuel


['.config', 'chunk_469.txt', 'chunk_922.txt', 'chunk_566.txt', 'chunk_31.txt', 'chunk_819.txt', 'chunk_132.txt', 'chunk_551.txt', 'chunk_809.txt', 'chunk_83.txt', 'chunk_124.txt', 'chunk_866.txt', 'chunk_896.txt', 'chunk_440.txt', 'chunk_264.txt', 'chunk_604.txt', 'chunk_14.txt', 'chunk_270.txt', 'chunk_125.txt', 'chunk_678.txt', 'chunk_395.txt', 'chunk_825.txt', 'chunk_676.txt', 'chunk_199.txt', 'chunk_597.txt', 'chunk_165.txt', 'chunk_947.txt', 'chunk_427.txt', 'chunk_289.txt', 'chunk_767.txt', 'chunk_793.txt', 'chunk_399.txt', 'chunk_845.txt', 'chunk_769.txt', 'chunk_640.txt', 'chunk_932.txt', 'chunk_179.txt', 'chunk_111.txt', 'chunk_437.txt', 'chunk_517.txt', 'chunk_382.txt', 'chunk_863.txt', 'chunk_148.txt', 'chunk_931.txt', 'chunk_332.txt', 'chunk_189.txt', 'chunk_875.txt', 'chunk_467.txt', 'chunk_404.txt', 'chunk_706.txt', 'chunk_448.txt', 'chunk_581.txt', 'chunk_774.txt', 'chunk_147.txt', 'chunk_235.txt', 'chunk_716.txt', 'chunk_237.txt', 'chunk_488.txt', 'chunk_684.txt', 'chun

In [8]:
import pandas as pd

file_path = '/content/questions_reponses_generation.tsv'

# Lire un fichier TSV avec pandas
df = pd.read_csv(file_path, sep='\t')  # Spécifie '\t' comme séparateur
print(df.head())  # Affiche les premières lignes du fichier TSV



                                            Question  \
0                 Quelle est l'importance du texte ?   
1  Que signifie le terme "confluence" dans le tex...   
2  Quel type de technologie est mentionné dans le...   
3  Quel aspect des élections est examiné dans le ...   
4  Quel est un exemple spécifique utilisé dans le...   

                                                   A  \
0  Décrire l'impact de la technologie sur les éle...   
1                                         Séparation   
2                              Technologie émergente   
3                                      La logistique   
4                               Les machines à voter   

                                                   B  \
0  Identifier les dangers de la technologie dans ...   
1                                             Fusion   
2                               Technologie obsolète   
3                                      Les candidats   
4                                 Les médias s

In [12]:
from google.colab import files
file_path = '/content/rcm.tsv'
files.download(file_path)  # Télécharge le fichier sur votre machine

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [16]:
nombre_questions = df.shape[0]  # Le premier élément de .shape correspond au nombre de lignes
print(f"Le nombre de questions est : {nombre_questions}")


Le nombre de questions est : 10


In [17]:
import pandas as pd

# Spécifier le chemin de ton fichier TSV
file_path = '/content/rcm.tsv'

# Charger le fichier TSV dans un DataFrame pandas
df = pd.read_csv(file_path, sep='\t')  # Le séparateur est '\t' pour les fichiers TSV


ParserError: Error tokenizing data. C error: Expected 22 fields in line 31, saw 23


In [15]:
nombre_questions = df1.shape[0]  # Le premier élément de .shape correspond au nombre de lignes
print(f"Le nombre de questions est : {nombre_questions}")


NameError: name 'df1' is not defined

In [ ]:
print(2500-1363)

1137


In [ ]:
import requests
from bs4 import BeautifulSoup
import time

urls = [
    "https://oasis-open.github.io/cti-documentation/",
    "https://capec.mitre.org/",
    "https://cwe.mitre.org/documents/vulnerability_theory/intro.html"
]

with open("sites_mcq.txt", "w", encoding="utf-8") as fichier_titres:
    for url in urls:
        print(f"Traitement de {url}...")

        try:
            response = requests.get(url)
            response.raise_for_status()
        except requests.exceptions.RequestException as e:
            print(f"Erreur lors de la requête vers {url}: {e}")
            continue

        soup = BeautifulSoup(response.content, 'html.parser')
        titres = soup.find_all('h2')

        for titre in titres:
            fichier_titres.write(titre.text.strip() + "\n")  # Ecriture dans le fichier

        time.sleep(2)

print("Extraction terminée ! Les titres sont dans 'sites_mcq.txt'")

Traitement de https://oasis-open.github.io/cti-documentation/...
Traitement de https://capec.mitre.org/...
Traitement de https://cwe.mitre.org/documents/vulnerability_theory/intro.html...
Extraction terminée ! Les titres sont dans 'titres.txt'


In [ ]:
# Ouvrir le fichier en mode lecture ('r')
fichier = open("sites_mcq.txt", "r")

# Lire le contenu du fichier
contenu = fichier.read()
print(contenu)

# Fermer le fichier (toujours important !)
fichier.close()

Introduction to Vulnerability Theory
Introduction to Vulnerability Theory



In [11]:
# convertir le fichier  rcm.txt en rcm.tsv
# Spécifiez les chemins d'accès des fichiers
input_file_path = 'rcm.txt'  # Remplacez par le chemin de votre fichier TXT
output_file_path = 'rcm.tsv'  # Chemin pour le fichier de sortie TSV

# Ouvrir le fichier TXT en mode lecture
with open(input_file_path, 'r') as infile:
    # Lire le contenu du fichier
    lines = infile.readlines()

# Ouvrir le fichier TSV en mode écriture
with open(output_file_path, 'w') as outfile:
    for line in lines:
        # Remplacez les espaces (ou d'autres séparateurs) par des tabulations
        tsv_line = line.replace(' ', '\t')  # Remplacez par le séparateur que vous souhaitez
        outfile.write(tsv_line)


In [18]:
# Spécifiez le chemin d'accès du fichier TSV
file_path = 'rcm.tsv'  # Remplacez par le chemin de votre fichier TSV

# Initialiser un compteur pour les questions
question_count = 0

# Ouvrir le fichier TSV en mode lecture
with open(file_path, 'r') as infile:
    for line in infile:
        # Incrémentez le compteur pour chaque ligne
        question_count += 1

# Afficher le nombre de questions
print(f'Nombre de questions dans le fichier TSV : {question_count}')


Nombre de questions dans le fichier TSV : 4999
